In [1]:
# Basic Libraries
import pandas as pd
import numpy as np
from scipy import stats

# Data Visualization
import matplotlib.pyplot as plt
import seaborn as sns

# Machine Learning
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler, MinMaxScaler, RobustScaler
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import accuracy_score, precision_score, recall_score, f1_score, roc_auc_score, confusion_matrix, classification_report
from sklearn.utils import resample

# For data manipulation
import pandas as pd
import numpy as np

# For splitting the data
from sklearn.model_selection import train_test_split

# For resampling (handling class imbalance)
from imblearn.over_sampling import SMOTE, ADASYN, BorderlineSMOTE
from imblearn.combine import SMOTEENN, SMOTETomek

# For scaling numeric features
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler

from sklearn.model_selection import StratifiedKFold, GridSearchCV
import lightgbm as lgb
import xgboost as xgb
from catboost import CatBoostClassifier

# # Configurations (optional)
pd.options.display.max_columns = None

import warnings
warnings.filterwarnings('ignore')



In [24]:
def preprocess_data(train, test):
    """
    Preprocesses train and test datasets with streamlined transformations and appropriate resampling.

    Parameters:
        train (DataFrame): Training dataset.
        test (DataFrame): Testing dataset.

    Returns:
        train (DataFrame): Preprocessed training dataset.
        test (DataFrame): Preprocessed testing dataset.
    """
    # Step 1: Drop 'ID' and 'Loan_ID' as they are unique identifiers
    train.drop(['ID', 'Loan_ID'], axis=1, inplace=True)
    test.drop(['ID', 'Loan_ID'], axis=1, inplace=True)

    # Step 2: Replace '3+' with 3 in 'Dependents' and convert to float
    train['Dependents'] = train['Dependents'].replace('3+', 3).astype(float)
    test['Dependents'] = test['Dependents'].replace('3+', 3).astype(float)

    # Step 3: Handle missing values (if any)
    # Although your dataset does not have missing values, this is good practice
    numeric_cols = ['ApplicantIncome', 'CoapplicantIncome', 'LoanAmount', 'Loan_Amount_Term', 'Total_Income']
    for col in numeric_cols:
        train[col].fillna(train[col].median(), inplace=True)
        test[col].fillna(test[col].median(), inplace=True)

    categorical_cols = ['Credit_History', 'Self_Employed', 'Education', 'Gender', 'Married']
    for col in categorical_cols:
        train[col].fillna(train[col].mode()[0], inplace=True)
        test[col].fillna(test[col].mode()[0], inplace=True)

    # Ensure no NaN values remain in the dataset
    train.fillna(0, inplace=True)
    test.fillna(0, inplace=True)

    # Step 4: One-Hot Encode 'Property_Area'
    train = pd.get_dummies(train, columns=['Property_Area'], drop_first=True)
    test = pd.get_dummies(test, columns=['Property_Area'], drop_first=True)

    # Step 5: Add feature interactions with descriptive headers
    for df in [train, test]:
        # Basic interactions
        df['Loan_to_Income_Ratio'] = df['LoanAmount'] / (df['ApplicantIncome'] + df['CoapplicantIncome'] + 1e-6)
        df['Income_per_Dependent'] = df['Total_Income'] / (df['Dependents'] + 1)
        df['LoanAmount_per_Term'] = df['LoanAmount'] / (df['Loan_Amount_Term'] + 1e-6)
        df['EMI'] = df['LoanAmount'] / (df['Loan_Amount_Term'] + 1e-6)
        df['EMI_to_Income_Ratio'] = df['EMI'] / df['Total_Income']
        df['Debt_to_Income_Ratio'] = df['LoanAmount'] / (df['Total_Income'] + 1e-6)
        df['all_income'] = df['ApplicantIncome'] + df['CoapplicantIncome'] + df['Total_Income']
        df['loan_to_all_income_ratio'] = df['LoanAmount'] / df['all_income']
        df['all_Income_per_Dependent'] = df['all_income'] / (df['Dependents'] + 1)

        # Additional interactions
        df['Dependents_Credit_History_Interaction'] = df['Dependents'] * df['Credit_History']
        df['Income_LoanAmount_Interaction'] = df['Total_Income'] * df['LoanAmount']
        df['all_Income_LoanAmount_Interaction'] = df['all_income'] * df['LoanAmount']
        df['Credit_History_LoanAmount'] = df['Credit_History'] * df['LoanAmount']
        df['Credit_History_Income_Interaction'] = df['Credit_History'] * df['Total_Income']
        df['Credit_History_all_Income_Interaction'] = df['Credit_History'] * df['all_income']
        df['loan_to_income_ratio'] = df['LoanAmount'] / (df['Total_Income'] + 1e-6)
        df['income_per_year_emp'] = df['ApplicantIncome'] / (df['Loan_Amount_Term'] + 1e-6)
        df['coapplicant_income_per_year_emp'] = df['CoapplicantIncome'] / (df['Loan_Amount_Term'] + 1e-6)
        df['all_income_per_year_emp'] = df['all_income'] / (df['Loan_Amount_Term'] + 1e-6)
        df['Coapplicant_Income_Ratio'] = df['CoapplicantIncome'] / df['Total_Income']
        df['Applicant_Income_Ratio'] = df['ApplicantIncome'] / df['Total_Income']
        df['TotalIncome_LoanAmount_Ratio'] = df['Total_Income'] / (df['LoanAmount'] + 1e-6)
        df['all_Income_LoanAmount_Ratio'] = df['all_income'] / (df['LoanAmount'] + 1e-6)
        df['CreditHistory_LoanTerm_Interaction'] = df['Credit_History'] * df['Loan_Amount_Term']
        df['Education_LoanAmount_Interaction'] = df['Education'] * df['LoanAmount']
        df['SelfEmployed_Income_Interaction'] = df['Self_Employed'] * df['Total_Income']

        # Squared and log-transformed features
        df['ApplicantIncome_Squared'] = df['ApplicantIncome'] ** 2
        df['all_income_Squared'] = df['all_income'] ** 2
        df['LoanAmount_Squared'] = df['LoanAmount'] ** 2
        df['Log_LoanAmount_per_Term'] = np.log1p(df['LoanAmount_per_Term'])
        df['Log_ApplicantIncome'] = np.log1p(df['ApplicantIncome'])
        df['Log_CoapplicantIncome'] = np.log1p(df['CoapplicantIncome'])
        df['Log_LoanAmount'] = np.log1p(df['LoanAmount'])
        df['Log_Total_Income'] = np.log1p(df['Total_Income'])

        # Dependents and loan-based interactions
        df['Dependents_TotalIncome_Interaction'] = df['Dependents'] * df['Total_Income']
        df['Dependents_LoanAmount_Interaction'] = df['Dependents'] * df['LoanAmount']
        df['LoanAmount_to_Term_Ratio'] = df['LoanAmount'] / (df['Loan_Amount_Term'] + 1e-6)

        # Feature interactions with Gender and Married
        df['Gender_ApplicantIncome'] = df['Gender'] * df['ApplicantIncome']
        df['Married_CoapplicantIncome'] = df['Married'] * df['CoapplicantIncome']
        df['Married_Total_Income'] = df['Married'] * df['Total_Income']
        df['Gender_Married_Interaction'] = df['Gender'] * df['Married']

    return train, test

from sklearn.utils import resample
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, MinMaxScaler, RobustScaler
from imblearn.over_sampling import SMOTE, ADASYN, BorderlineSMOTE
from imblearn.combine import SMOTEENN, SMOTETomek

# Helper function for oversampling
def resample_minority_class(X, y):
    # Concatenate X and y for resampling
    data = pd.concat([X, y], axis=1)
    minority_class = data[y.name].value_counts().idxmin()  # Find the minority class
    minority_data = data[data[y.name] == minority_class]
    majority_data = data[data[y.name] != minority_class]

    # Oversample the minority class
    minority_upsampled = resample(minority_data,
                                  replace=True,  # Sample with replacement
                                  n_samples=len(majority_data),  # Match majority class size
                                  random_state=42)

    # Combine majority data with upsampled minority data
    upsampled_data = pd.concat([majority_data, minority_upsampled])

    return upsampled_data.drop(columns=[y.name]), upsampled_data[y.name]

# Helper function for undersampling
def resample_majority_class(X, y):
    # Concatenate X and y for resampling
    data = pd.concat([X, y], axis=1)
    minority_class = data[y.name].value_counts().idxmin()  # Find the minority class
    minority_data = data[data[y.name] == minority_class]
    majority_data = data[data[y.name] != minority_class]

    # Undersample the majority class
    majority_downsampled = resample(majority_data,
                                    replace=False,  # Sample without replacement
                                    n_samples=len(minority_data),  # Match minority class size
                                    random_state=42)

    # Combine minority data with downsampled majority data
    downsampled_data = pd.concat([minority_data, majority_downsampled])

    return downsampled_data.drop(columns=[y.name]), downsampled_data[y.name]

# Main function for resampling and scaling
def resample_split(train, test, resampling_method='SMOTE', scaling_option=None):
    """
    Splits the data into training and testing sets, handles class imbalance, and scales features appropriately.

    Parameters:
        train (DataFrame): Preprocessed training dataset.
        test (DataFrame): Preprocessed testing dataset.
        resampling_method (str): Resampling technique to handle class imbalance.
                                 Options: 'SMOTE', 'ADASYN', 'Borderline-SMOTE', 'SMOTEENN', 'SMOTETomek', 'oversample', 'undersample'.
        scaling_option (str): Scaling technique for continuous features.
                              Options: 'standard', 'minmax', 'robust', or None.

    Returns:
        X_train_res (array): Resampled training features.
        y_train_res (array): Resampled training labels.
        X_test (array): Scaled testing features.
        y_test (array): Original testing labels.
        test_scaled (array): Scaled test dataset features.
    """
    # Step 1: Create X and y
    X = train.drop('Loan_Status', axis=1)
    y = train['Loan_Status']
    test = test.copy()

    # Step 2: Align columns between train and test
    X, test = X.align(test, join='left', axis=1, fill_value=0)

    # Step 3: Split data
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.4, random_state=1, stratify=y)

    # Step 4: Handle class imbalance
    if resampling_method == 'SMOTE':
        resampler = SMOTE(random_state=42)
        X_train_res, y_train_res = resampler.fit_resample(X_train, y_train)
    elif resampling_method == 'ADASYN':
        resampler = ADASYN(random_state=42)
        X_train_res, y_train_res = resampler.fit_resample(X_train, y_train)
    elif resampling_method == 'Borderline-SMOTE':
        resampler = BorderlineSMOTE(random_state=42)
        X_train_res, y_train_res = resampler.fit_resample(X_train, y_train)
    elif resampling_method == 'SMOTEENN':
        resampler = SMOTEENN(random_state=42)
        X_train_res, y_train_res = resampler.fit_resample(X_train, y_train)
    elif resampling_method == 'SMOTETomek':
        resampler = SMOTETomek(random_state=42)
        X_train_res, y_train_res = resampler.fit_resample(X_train, y_train)
    elif resampling_method == 'oversample':
        # Oversample the minority class
        X_train_res, y_train_res = resample_minority_class(X_train, y_train)
    elif resampling_method == 'undersample':
        # Undersample the majority class
        X_train_res, y_train_res = resample_majority_class(X_train, y_train)
    else:
        raise ValueError(f"Invalid resampling method: {resampling_method}")

    # Step 5: Scale numeric features (optional, based on model requirements)
    if scaling_option:
        # List of binary columns (do not scale these)
        binary_cols = ['Gender', 'Married', 'Education', 'Self_Employed', 'Credit_History']
        # Include 'Property_Area' dummies
        binary_cols += [col for col in X_train_res.columns if 'Property_Area_' in col]

        # Columns to scale
        cols_to_scale = [col for col in X_train_res.columns if col not in binary_cols]

        # Apply scaler
        scaler = None
        if scaling_option == 'standard':
            scaler = StandardScaler()
        elif scaling_option == 'minmax':
            scaler = MinMaxScaler()
        elif scaling_option == 'robust':
            scaler = RobustScaler()
        else:
            raise ValueError(f"Invalid scaling option: {scaling_option}")

        if scaler:
            # Ensure that X_train_res, X_test, test are DataFrames
            if not isinstance(X_train_res, pd.DataFrame):
                X_train_res = pd.DataFrame(X_train_res, columns=X.columns)
            if not isinstance(X_test, pd.DataFrame):
                X_test = pd.DataFrame(X_test, columns=X.columns)
            if not isinstance(test, pd.DataFrame):
                test = pd.DataFrame(test, columns=X.columns)

            # Apply scaling only to continuous features
            X_train_res[cols_to_scale] = scaler.fit_transform(X_train_res[cols_to_scale])
            X_test[cols_to_scale] = scaler.transform(X_test[cols_to_scale])
            test[cols_to_scale] = scaler.transform(test[cols_to_scale])

    # Convert back to arrays for modeling
    X_train_res = X_train_res.values
    X_test = X_test.values
    test_scaled = test.values

    return X_train_res, y_train_res, X_test, y_test, test_scaled


In [25]:
train = pd.read_csv('data/Train.csv')
test = pd.read_csv('data/Test.csv')

# Preprocess the data
# train, test = preprocess_data(train, test)


In [26]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.feature_selection import SelectKBest, f_classif, mutual_info_classif
import pandas as pd
import numpy as np

def preprocess_data_with_feature_selection(train, test, target_col='Loan_Status', method='model', k=20):
    """
    Preprocesses train and test datasets with streamlined transformations and feature selection.

    Parameters:
        train (DataFrame): Training dataset.
        test (DataFrame): Testing dataset.
        target_col (str): Name of the target column.
        method (str): Feature selection method - 'model', 'filter', or 'embedded'.
        k (int): Number of top features to select.

    Returns:
        train_selected (DataFrame): Preprocessed and selected training dataset.
        test_selected (DataFrame): Preprocessed and selected testing dataset.
    """
    # Separate target variable
    y_train = train[target_col]
    train = train.drop(target_col, axis=1)

    # Preprocess train and test (original preprocessing steps)
    train, test = preprocess_data(train, test)

    # Feature selection
    if method == 'filter':
        # Univariate feature selection using ANOVA F-test or mutual information
        selector = SelectKBest(score_func=f_classif, k=k)
        train_selected = selector.fit_transform(train, y_train)
        test_selected = selector.transform(test)
        
        # Get selected feature names
        selected_features = train.columns[selector.get_support()]
        train_selected = pd.DataFrame(train_selected, columns=selected_features)
        test_selected = pd.DataFrame(test_selected, columns=selected_features)

    elif method == 'model':
        # Use a RandomForest or LightGBM model to rank features
        model = RandomForestClassifier(random_state=42)
        model.fit(train, y_train)
        
        # Get feature importance
        feature_importances = pd.DataFrame({
            'feature': train.columns,
            'importance': model.feature_importances_
        }).sort_values(by='importance', ascending=False)

        # Select top k features
        selected_features = feature_importances.head(k)['feature']
        train_selected = train[selected_features]
        test_selected = test[selected_features]

    elif method == 'embedded':
        # Use L1-regularized model (e.g., Lasso or Logistic Regression)
        from sklearn.linear_model import LogisticRegression
        model = LogisticRegression(penalty='l1', solver='liblinear', random_state=42)
        model.fit(train, y_train)
        
        # Get non-zero coefficients
        selected_features = train.columns[model.coef_[0] != 0]
        train_selected = train[selected_features]
        test_selected = test[selected_features]

    else:
        raise ValueError(f"Invalid feature selection method: {method}")

    # Add target back to train
    train_selected[target_col] = y_train

    return train_selected, test_selected


In [27]:
# Example Usage
train_selected, test_selected = preprocess_data_with_feature_selection(
    train, test, target_col='Loan_Status', method='model', k=30
)

print("Selected Features (Train):", train_selected.columns)
print("Selected Features (Test):", test_selected.columns)


Selected Features (Train): Index(['all_Income_per_Dependent', 'all_income_per_year_emp',
       'Loan_to_Income_Ratio', 'income_per_year_emp',
       'all_Income_LoanAmount_Interaction', 'all_Income_LoanAmount_Ratio',
       'loan_to_all_income_ratio', 'all_income',
       'Credit_History_all_Income_Interaction', 'Applicant_Income_Ratio',
       'all_income_Squared', 'Gender_ApplicantIncome', 'ApplicantIncome',
       'ApplicantIncome_Squared', 'Loan_Amount_Term', 'Log_ApplicantIncome',
       'Log_LoanAmount_per_Term', 'LoanAmount_to_Term_Ratio',
       'LoanAmount_per_Term', 'EMI', 'CreditHistory_LoanTerm_Interaction',
       'EMI_to_Income_Ratio', 'Coapplicant_Income_Ratio',
       'coapplicant_income_per_year_emp', 'Log_CoapplicantIncome',
       'CoapplicantIncome', 'Income_LoanAmount_Interaction',
       'Married_CoapplicantIncome', 'loan_to_income_ratio',
       'Debt_to_Income_Ratio', 'Loan_Status'],
      dtype='object')
Selected Features (Test): Index(['all_Income_per_Depende

In [28]:
train_selected.head()

all_Income_per_Dependent  all_income_per_year_emp  Loan_to_Income_Ratio  \
0              14328.000000                39.471074              0.002041   
1              10007.458782                27.047186              0.046913   
2              11303.472511                32.481243              0.003205   
3               3900.000000                10.863510              1.546667   
4               5904.500000                31.744624              0.002109   

   income_per_year_emp  all_Income_LoanAmount_Interaction  \
0            22.942149                       2.435760e+05   
1             0.405405                       1.881402e+06   
2            14.336207                       1.921590e+05   
3             0.417827                       9.048000e+05   
4            21.663978                       2.007530e+05   

   all_Income_LoanAmount_Ratio  loan_to_all_income_ratio    all_income  \
0                   842.823480                  0.001186  14328.000000   
1                    53.231163                  0.018786  10007.458782   
2                   664.910109                  0.001504  11303.472511   
3                    16.810345                  0.059487   3900.000000   
4                   694.647018                  0.001440  11809.000000   

   Credit_History_all_Income_Interaction  Applicant_Income_Ratio  \
0                           14328.000000                1.388000   
1                           10007.458782                0.025000   
2                           11303.472511                0.831500   
3                            3900.000000                0.040000   
4                           11809.000000                2.149067   

   all_income_Squared  Gender_ApplicantIncome  ApplicantIncome  \
0        2.052916e+08                    8328             8328   
1        1.001492e+08                     150              150   
2        1.277685e+08                       0             4989   
3        1.521000e+07                     150              150   
4        1.394525e+08                    8059             8059   

   ApplicantIncome_Squared  Loan_Amount_Term  Log_ApplicantIncome  \
0                 69355584               363             9.027499   
1                    22500               370             5.017280   
2                 24890121               348             8.515191   
3                    22500               359             5.017280   
4                 64947481               372             8.994669   

   Log_LoanAmount_per_Term  LoanAmount_to_Term_Ratio  LoanAmount_per_Term  \
0                 0.045768                  0.046832             0.046832   
1                 0.410856                  0.508108             0.508108   
2                 0.047695                  0.048851             0.048851   
3                 0.498494                  0.646240             0.646240   
4                 0.044685                  0.045699             0.045699   

        EMI  CreditHistory_LoanTerm_Interaction  EMI_to_Income_Ratio  \
0  0.046832                                 363             0.000008   
1  0.508108                                 370             0.000085   
2  0.048851                                 348             0.000008   
3  0.646240                                 359             0.000172   
4  0.045699                                 372             0.000012   

   Coapplicant_Income_Ratio  coapplicant_income_per_year_emp  \
0                  0.000000                         0.000000   
1                  0.642910                        10.425564   
2                  0.052412                         0.903657   
3                  0.000000                         0.000000   
4                  0.000000                         0.000000   

   Log_CoapplicantIncome  CoapplicantIncome  Income_LoanAmount_Interaction  \
0               0.000000           0.000000                         102000   
1               8.258023        3857.458782                     

In [29]:
test_selected.head()

all_Income_per_Dependent  all_income_per_year_emp  Loan_to_Income_Ratio  \
0              22761.075952                61.350609              0.011216   
1              13478.718887                36.135975              0.002273   
2              14441.900354                38.718231              0.002014   
3               6150.000000                17.621776              1.646667   
4              12112.000000              1009.333249              0.002033   

   income_per_year_emp  all_Income_LoanAmount_Interaction  \
0            42.830189                       4.279082e+06   
1            17.646113                       2.291382e+05   
2            21.096515                       2.455123e+05   
3             0.429799                       1.519050e+06   
4           696.833275                       2.059040e+05   

   all_Income_LoanAmount_Ratio  loan_to_all_income_ratio    all_income  \
0                   121.069552                  0.008260  22761.075952   
1                   792.865770                  0.001261  13478.718887   
2                   849.523500                  0.001177  14441.900354   
3                    24.898785                  0.040163   6150.000000   
4                   712.470546                  0.001404  12112.000000   

   Credit_History_all_Income_Interaction  Applicant_Income_Ratio  \
0                           22761.075952                2.648333   
1                               0.000000                1.097000   
2                           14441.900354                1.311500   
3                            6150.000000                0.025000   
4                           12112.000000                2.229867   

   all_income_Squared  Gender_ApplicantIncome  ApplicantIncome  \
0        5.180666e+08                   15890            15890   
1        1.816759e+08                    6582             6582   
2        2.085685e+08                       0             7869   
3        3.782250e+07                     150              150   
4        1.467005e+08                    8362             8362   

   ApplicantIncome_Squared  Loan_Amount_Term  Log_ApplicantIncome  \
0                252492100               371             9.673508   
1                 43322724               373             8.792246   
2                 61921161               373             8.970813   
3                    22500               349             5.017280   
4                 69923044                12             9.031572   

   Log_LoanAmount_per_Term  LoanAmount_to_Term_Ratio  LoanAmount_per_Term  \
0                 0.409947                  0.506739             0.506739   
1                 0.044568                  0.045576             0.045576   
2                 0.044568                  0.045576             0.045576   
3                 0.535169                  0.707736             0.707736   
4                 0.882389                  1.416667             1.416667   

        EMI  CreditHistory_LoanTerm_Interaction  EMI_to_Income_Ratio  \
0  0.506739                                 371             0.000084   
1  0.045576                                   0             0.000008   
2  0.045576                                 373             0.000008   
3  0.707736                                 349             0.000118   
4  1.416667                                  12             0.000378   

   Coapplicant_Income_Ratio  coapplicant_income_per_year_emp  \
0                  0.145179                         2.347914   
1                  0.149453                         2.404072   
2                  0.095483                         1.535926   
3                  0.000000                         0.000000   
4                  0.000000                         0.000000   

   Log_CoapplicantIncome  CoapplicantIncome  Income_LoanAmount_Interaction  \
0               6.770877         871.075952                        1128000   
1               6.799857         896.718887                     

In [36]:
# Resample, split, and scale the data
X_train_res, y_train_res, X_test, y_test, test_scaled = resample_split(
    train_selected,
    test_selected,
    resampling_method='SMOTE',
    scaling_option='minmax'
)

In [37]:

from lightgbm import LGBMClassifier
from sklearn.model_selection import StratifiedKFold, GridSearchCV
from imblearn.pipeline import Pipeline
from imblearn.over_sampling import SMOTE

def grid_search_lightgbm_with_smote(X_train, y_train, X_test, y_test):
    # Define a narrowed parameter grid
    param_grid = {
        'lgbm__learning_rate': [0.02, 0.03229, 0.05],
        'lgbm__num_leaves': [20, 24, 28],
        'lgbm__max_depth': [12, 15, 18],
        'lgbm__min_data_in_leaf': [20, 25, 30],
        'lgbm__feature_fraction': [0.6, 0.6236, 0.65],
        'lgbm__bagging_fraction': [0.95, 0.9597, 0.97],
        'lgbm__bagging_freq': [2, 3, 4]
    }

    # Create a pipeline with SMOTE and LGBMClassifier
    pipeline = Pipeline([
        ('smote', SMOTE(random_state=42)),
        ('lgbm', LGBMClassifier(
            objective='binary',
            n_estimators=3000,
            metric='binary_logloss',
            boosting_type='gbdt',
            random_state=42,
            verbose=-1
        ))
    ])

    # Stratified K-Fold
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

    # Grid Search
    grid_search = GridSearchCV(
        estimator=pipeline,
        param_grid=param_grid,
        scoring='roc_auc',
        cv=skf,
        n_jobs=-1,
        verbose=1
    )

    # Fit the model using resampled training data
    grid_search.fit(X_train, y_train)

    print("Best Parameters:", grid_search.best_params_)
    print("Best ROC-AUC (Cross-Validation):", grid_search.best_score_)

    # Use the best model to predict on the test set
    best_model = grid_search.best_estimator_
    y_pred = best_model.predict_proba(X_test)[:, 1]

    from sklearn.metrics import roc_auc_score
    roc_auc = roc_auc_score(y_test, y_pred)
    print("Test ROC-AUC:", roc_auc)

    return best_model


In [38]:
from xgboost import XGBClassifier

def grid_search_xgboost_with_smote(X_train, y_train, X_test, y_test):
    # Define a narrowed parameter grid
    param_grid = {
        'xgb__learning_rate': [0.02, 0.05, 0.1],
        'xgb__max_depth': [3, 5, 7],
        'xgb__n_estimators': [100, 200, 300],
        'xgb__subsample': [0.8, 0.9],
        'xgb__colsample_bytree': [0.8, 0.9]
    }

    # Create a pipeline with SMOTE and XGBClassifier
    pipeline = Pipeline([
        ('smote', SMOTE(random_state=42)),
        ('xgb', XGBClassifier(
            objective='binary:logistic',
            random_state=42,
            use_label_encoder=False,
            eval_metric='logloss'
        ))
    ])

    # Stratified K-Fold
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)

    # Grid Search
    grid_search = GridSearchCV(
        estimator=pipeline,
        param_grid=param_grid,
        scoring='roc_auc',
        cv=skf,
        n_jobs=-1,
        verbose=1
    )

    # Fit the model using resampled training data
    grid_search.fit(X_train, y_train)

    print("Best Parameters:", grid_search.best_params_)
    print("Best ROC-AUC (Cross-Validation):", grid_search.best_score_)

    # Use the best model to predict on the test set
    best_model = grid_search.best_estimator_
    y_pred = best_model.predict_proba(X_test)[:, 1]

    from sklearn.metrics import roc_auc_score
    roc_auc = roc_auc_score(y_test, y_pred)
    print("Test ROC-AUC:", roc_auc)

    return best_model


In [ ]:
import optuna
from lightgbm import LGBMClassifier
from sklearn.metrics import roc_auc_score

def objective_lightgbm(trial):
    # Suggest hyperparameters
    params = {
        'objective': 'binary',
        'metric': 'auc',
        'boosting_type': 'gbdt',
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-3, 0.1),
        'num_leaves': trial.suggest_int('num_leaves', 20, 100),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'min_data_in_leaf': trial.suggest_int('min_data_in_leaf', 10, 100),
        'feature_fraction': trial.suggest_uniform('feature_fraction', 0.5, 0.9),
        'bagging_fraction': trial.suggest_uniform('bagging_fraction', 0.5, 1.0),
        'bagging_freq': trial.suggest_int('bagging_freq', 1, 10),
    }

    # Stratified K-Fold Cross-Validation
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    cv_scores = []

    for train_idx, val_idx in skf.split(X_train_res, y_train_res):
        X_train_fold, X_val_fold = X_train_res[train_idx], X_train_res[val_idx]
        y_train_fold, y_val_fold = y_train_res[train_idx], y_train_res[val_idx]

        model = LGBMClassifier(**params, random_state=42)
        model.fit(X_train_fold, y_train_fold, eval_set=[(X_val_fold, y_val_fold)], early_stopping_rounds=50, verbose=False)
        preds = model.predict_proba(X_val_fold)[:, 1]
        cv_scores.append(roc_auc_score(y_val_fold, preds))

    # Return the average ROC-AUC across folds
    return np.mean(cv_scores)

# Create Optuna study and optimize
study = optuna.create_study(direction='maximize')
study.optimize(objective_lightgbm, n_trials=50)

# Best parameters and score
print("Best Parameters (LightGBM):", study.best_params)
print("Best AUC (LightGBM):", study.best_value)

# Train final model with best parameters
best_params = study.best_params
final_model_lgb = LGBMClassifier(**best_params, random_state=42)
final_model_lgb.fit(X_train_res, y_train_res)


In [41]:
import xgboost as xgb

def objective_xgboost(trial):
    # Suggest hyperparameters
    params = {
        'objective': 'binary:logistic',
        'eval_metric': 'auc',
        'n_estimators': trial.suggest_int('n_estimators', 100, 1000),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-3, 0.1),
        'max_depth': trial.suggest_int('max_depth', 3, 15),
        'subsample': trial.suggest_uniform('subsample', 0.5, 1.0),
        'colsample_bytree': trial.suggest_uniform('colsample_bytree', 0.5, 1.0),
        'min_child_weight': trial.suggest_int('min_child_weight', 1, 10),
    }

    # Stratified K-Fold Cross-Validation
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    cv_scores = []

    for train_idx, val_idx in skf.split(X_train_res, y_train_res):
        X_train_fold, X_val_fold = X_train_res[train_idx], X_train_res[val_idx]
        y_train_fold, y_val_fold = y_train_res[train_idx], y_train_res[val_idx]

        model = xgb.XGBClassifier(**params, random_state=42, use_label_encoder=False)
        model.fit(X_train_fold, y_train_fold, eval_set=[(X_val_fold, y_val_fold)])
        preds = model.predict_proba(X_val_fold)[:, 1]
        cv_scores.append(roc_auc_score(y_val_fold, preds))

    # Return the average ROC-AUC across folds
    return np.mean(cv_scores)

# Create Optuna study and optimize
study = optuna.create_study(direction='maximize')
study.optimize(objective_xgboost, n_trials=50)

# Best parameters and score
print("Best Parameters (XGBoost):", study.best_params)
print("Best AUC (XGBoost):", study.best_value)

# Train final model with best parameters
best_params = study.best_params
final_model_xgb = xgb.XGBClassifier(**best_params, random_state=42, use_label_encoder=False)
final_model_xgb.fit(X_train_res, y_train_res)


[I 2024-11-23 21:07:23,434] A new study created in memory with name: no-name-de6427c1-8950-46af-b6d8-312a62046deb


[0]	validation_0-auc:0.69165
[1]	validation_0-auc:0.71084
[2]	validation_0-auc:0.75995
[3]	validation_0-auc:0.77126
[4]	validation_0-auc:0.77228
[5]	validation_0-auc:0.79120
[6]	validation_0-auc:0.80173
[7]	validation_0-auc:0.79525
[8]	validation_0-auc:0.80402
[9]	validation_0-auc:0.80751
[10]	validation_0-auc:0.81150
[11]	validation_0-auc:0.81316
[12]	validation_0-auc:0.81306
[13]	validation_0-auc:0.81795
[14]	validation_0-auc:0.81937
[15]	validation_0-auc:0.82310
[16]	validation_0-auc:0.82083
[17]	validation_0-auc:0.82232
[18]	validation_0-auc:0.82582
[19]	validation_0-auc:0.82679
[20]	validation_0-auc:0.82852
[21]	validation_0-auc:0.82948
[22]	validation_0-auc:0.82941
[23]	validation_0-auc:0.82879
[24]	validation_0-auc:0.82991
[25]	validation_0-auc:0.83318
[26]	validation_0-auc:0.83495
[27]	validation_0-auc:0.83694
[28]	validation_0-auc:0.83699
[29]	validation_0-auc:0.83841
[30]	validation_0-auc:0.83807
[31]	validation_0-auc:0.83790
[32]	validation_0-auc:0.84037
[33]	validation_0-au

[I 2024-11-23 21:07:28,023] Trial 0 finished with value: 0.9050182811609677 and parameters: {'n_estimators': 537, 'learning_rate': 0.08685763987080015, 'max_depth': 4, 'subsample': 0.6836808538335686, 'colsample_bytree': 0.6690301285794469, 'min_child_weight': 8}. Best is trial 0 with value: 0.9050182811609677.


[0]	validation_0-auc:0.73806
[1]	validation_0-auc:0.75497
[2]	validation_0-auc:0.77547
[3]	validation_0-auc:0.78352
[4]	validation_0-auc:0.80101
[5]	validation_0-auc:0.80726
[6]	validation_0-auc:0.81203
[7]	validation_0-auc:0.81502
[8]	validation_0-auc:0.81985
[9]	validation_0-auc:0.82296
[10]	validation_0-auc:0.82383
[11]	validation_0-auc:0.83271
[12]	validation_0-auc:0.83426
[13]	validation_0-auc:0.83552
[14]	validation_0-auc:0.83268
[15]	validation_0-auc:0.83666
[16]	validation_0-auc:0.84061
[17]	validation_0-auc:0.84306
[18]	validation_0-auc:0.84643
[19]	validation_0-auc:0.84813
[20]	validation_0-auc:0.84907
[21]	validation_0-auc:0.84897
[22]	validation_0-auc:0.85083
[23]	validation_0-auc:0.85112
[24]	validation_0-auc:0.85109
[25]	validation_0-auc:0.85400
[26]	validation_0-auc:0.85539
[27]	validation_0-auc:0.85672
[28]	validation_0-auc:0.85792
[29]	validation_0-auc:0.85796
[30]	validation_0-auc:0.85847
[31]	validation_0-auc:0.85912
[32]	validation_0-auc:0.85933
[33]	validation_0-au

[I 2024-11-23 21:07:31,525] Trial 1 finished with value: 0.9035921361278998 and parameters: {'n_estimators': 245, 'learning_rate': 0.048783940584981984, 'max_depth': 9, 'subsample': 0.5317308857240053, 'colsample_bytree': 0.6104669784000554, 'min_child_weight': 8}. Best is trial 0 with value: 0.9050182811609677.


...

[I 2024-11-23 21:16:02,462] Trial 48 finished with value: 0.9316457842524496 and parameters: {'n_estimators': 531, 'learning_rate': 0.05605482630923885, 'max_depth': 14, 'subsample': 0.7901646618276682, 'colsample_bytree': 0.7129387062276996, 'min_child_weight': 2}. Best is trial 28 with value: 0.933148121105479.


[0]	validation_0-auc:0.74763
[1]	validation_0-auc:0.77648
[2]	validation_0-auc:0.80001
[3]	validation_0-auc:0.81303
[4]	validation_0-auc:0.83061
[5]	validation_0-auc:0.83443
[6]	validation_0-auc:0.84341
[7]	validation_0-auc:0.84832
[8]	validation_0-auc:0.85222
[9]	validation_0-auc:0.85416
[10]	validation_0-auc:0.85927
[11]	validation_0-auc:0.86376
[12]	validation_0-auc:0.86477
[13]	validation_0-auc:0.86759
[14]	validation_0-auc:0.87124
[15]	validation_0-auc:0.87671
[16]	validation_0-auc:0.87986
[17]	validation_0-auc:0.88184
[18]	validation_0-auc:0.88371
[19]	validation_0-auc:0.88354
[20]	validation_0-auc:0.88455
[21]	validation_0-auc:0.88521
[22]	validation_0-auc:0.88635
[23]	validation_0-auc:0.88640
[24]	validation_0-auc:0.88823
[25]	validation_0-auc:0.89001
[26]	validation_0-auc:0.89081
[27]	validation_0-auc:0.89120
[28]	validation_0-auc:0.89193
[29]	validation_0-auc:0.89228
[30]	validation_0-auc:0.89277
[31]	validation_0-auc:0.89317
[32]	validation_0-auc:0.89302
[33]	validation_0-au

[I 2024-11-23 21:16:09,234] Trial 49 finished with value: 0.9240277650277339 and parameters: {'n_estimators': 412, 'learning_rate': 0.08423782308579442, 'max_depth': 11, 'subsample': 0.7665335485258027, 'colsample_bytree': 0.6615597582076272, 'min_child_weight': 7}. Best is trial 28 with value: 0.933148121105479.


Best Parameters (XGBoost): {'n_estimators': 818, 'learning_rate': 0.025519080744339073, 'max_depth': 11, 'subsample': 0.7244069470995078, 'colsample_bytree': 0.5758485018927367, 'min_child_weight': 1}
Best AUC (XGBoost): 0.933148121105479


XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=0.5758485018927367, device=None,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, feature_types=None, gamma=None,
              grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=0.025519080744339073,
              max_bin=None, max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=11, max_leaves=None,
              min_child_weight=1, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=818, n_jobs=None,
              num_parallel_tree=None, random_state=42, ...)

In [42]:
# Predict on the test set
y_test_pred = final_model_xgb.predict(X_test)

# Function to print metrics
def print_metrics(y_true, y_pred, dataset_name):
    print(f"Metrics for {dataset_name}:")
    print("Accuracy:", accuracy_score(y_true, y_pred))
    print("Precision:", precision_score(y_true, y_pred, pos_label=1))  # Change 'Yes' to the positive label in your dataset
    print("Recall:", recall_score(y_true, y_pred, pos_label=1))
    print("F1 Score:", f1_score(y_true, y_pred, pos_label=1))
    print("\nClassification Report:\n", classification_report(y_true, y_pred))
    print("Confusion Matrix:\n", confusion_matrix(y_true, y_pred))
    print("\n" + "="*50 + "\n")

# Print metrics for test set
print_metrics(y_test, y_test_pred, "Test Set")

Metrics for Test Set:
Accuracy: 0.7610169491525424
Precision: 0.8344465648854962
Recall: 0.8896236012207528
F1 Score: 0.8611521418020679

Classification Report:
               precision    recall  f1-score   support

           0       0.18      0.12      0.14       394
           1       0.83      0.89      0.86      1966

    accuracy                           0.76      2360
   macro avg       0.51      0.50      0.50      2360
weighted avg       0.72      0.76      0.74      2360

Confusion Matrix:
 [[  47  347]
 [ 217 1749]]




In [34]:
from catboost import CatBoostClassifier

def objective_catboost(trial):
    # Suggest hyperparameters
    params = {
        'iterations': trial.suggest_int('iterations', 500, 2000),
        'learning_rate': trial.suggest_loguniform('learning_rate', 1e-3, 0.1),
        'depth': trial.suggest_int('depth', 4, 10),
        'l2_leaf_reg': trial.suggest_loguniform('l2_leaf_reg', 1e-2, 10.0),
        'bagging_temperature': trial.suggest_uniform('bagging_temperature', 0.0, 1.0),
        'random_strength': trial.suggest_uniform('random_strength', 0.0, 10.0)
    }

    # Stratified K-Fold Cross-Validation
    skf = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
    cv_scores = []

    for train_idx, val_idx in skf.split(X_train_res, y_train_res):
        X_train_fold, X_val_fold = X_train_res[train_idx], X_train_res[val_idx]
        y_train_fold, y_val_fold = y_train_res[train_idx], y_train_res[val_idx]

        model = CatBoostClassifier(**params, random_state=42, verbose=0)
        model.fit(X_train_fold, y_train_fold, eval_set=(X_val_fold, y_val_fold), early_stopping_rounds=50)
        preds = model.predict_proba(X_val_fold)[:, 1]
        cv_scores.append(roc_auc_score(y_val_fold, preds))

    # Return the average ROC-AUC across folds
    return np.mean(cv_scores)

# Create Optuna study and optimize
study = optuna.create_study(direction='maximize')
study.optimize(objective_catboost, n_trials=20)

# Best parameters and score
print("Best Parameters (CatBoost):", study.best_params)
print("Best AUC (CatBoost):", study.best_value)

# Train final model with best parameters
best_params = study.best_params
final_model_cat = CatBoostClassifier(**best_params, random_state=42, verbose=0)
final_model_cat.fit(X_train_res, y_train_res)


[I 2024-11-23 20:46:08,766] A new study created in memory with name: no-name-24476f0a-c28a-4a6a-bf0f-041a3dc9863c
[I 2024-11-23 20:46:45,799] Trial 0 finished with value: 0.8443000919615413 and parameters: {'iterations': 1404, 'learning_rate': 0.0012617913705019691, 'depth': 9, 'l2_leaf_reg': 0.5348100709718068, 'bagging_temperature': 0.37712282590604496, 'random_strength': 2.8819301600313665}. Best is trial 0 with value: 0.8443000919615413.
[I 2024-11-23 20:47:25,484] Trial 1 finished with value: 0.9380290662569152 and parameters: {'iterations': 951, 'learning_rate': 0.021773980821340393, 'depth': 10, 'l2_leaf_reg': 0.24817360984164608, 'bagging_temperature': 0.11196524383675577, 'random_strength': 2.3833324334438446}. Best is trial 1 with value: 0.9380290662569152.
[I 2024-11-23 20:47:41,303] Trial 2 finished with value: 0.9344781537964562 and parameters: {'iterations': 1398, 'learning_rate': 0.029647311836170177, 'depth': 7, 'l2_leaf_reg': 0.1064095357782081, 'bagging_temperature': 

Best Parameters (CatBoost): {'iterations': 951, 'learning_rate': 0.021773980821340393, 'depth': 10, 'l2_leaf_reg': 0.24817360984164608, 'bagging_temperature': 0.11196524383675577, 'random_strength': 2.3833324334438446}
Best AUC (CatBoost): 0.9380290662569152


In [35]:
# Predict on the test set
y_test_pred = final_model_cat.predict(X_test)

# Function to print metrics
def print_metrics(y_true, y_pred, dataset_name):
    print(f"Metrics for {dataset_name}:")
    print("Accuracy:", accuracy_score(y_true, y_pred))
    print("Precision:", precision_score(y_true, y_pred, pos_label=1))  # Change 'Yes' to the positive label in your dataset
    print("Recall:", recall_score(y_true, y_pred, pos_label=1))
    print("F1 Score:", f1_score(y_true, y_pred, pos_label=1))
    print("\nClassification Report:\n", classification_report(y_true, y_pred))
    print("Confusion Matrix:\n", confusion_matrix(y_true, y_pred))
    print("\n" + "="*50 + "\n")

# Print metrics for test set
print_metrics(y_test, y_test_pred, "Test Set")

Metrics for Test Set:
Accuracy: 0.760593220338983
Precision: 0.8321479374110953
Recall: 0.8926754832146491
F1 Score: 0.8613496932515338

Classification Report:
               precision    recall  f1-score   support

           0       0.16      0.10      0.12       394
           1       0.83      0.89      0.86      1966

    accuracy                           0.76      2360
   macro avg       0.50      0.50      0.49      2360
weighted avg       0.72      0.76      0.74      2360

Confusion Matrix:
 [[  40  354]
 [ 211 1755]]


